# Proyecto Boosting

En este proyecto vamos a crear un algoritmo supervisado aplicando la técnica de **Boosting** para clasificación con las siguientes líbrerias: 
* Scikit Learn
    * AdaBoostClassifier
    * GradientBoostingClassifier
* Xgboost
* Lightgbm  

Con los datos de los proyectos anteriores *04_decision_tree_diabetes* y *05_random_forest_diabetes* intentaremos automatizar los entrenamientos y luego cargar los datos para ver una comparativa con modelos anteriores y así tener una perspectiva de los mismos. Todo ello teniendo presente la modificación del análisis de datos en el proyecto *04_decision_tree_diabetes* para mejorar resultados.
Para obtener la mejor hipeparametrizacion de todos los modelos usaremos *RandomizedSearchCV* directamente sin utilizar los modelos base, que a diferencia de *GridSearchCV* el cual usa todas las combinaciones posibles de hiperparámetros, solo prueba combinaciones aleatorias en un espacio mayor de manera más rápida, por lo tanto lo hace más indicado para técnicas de boosting.

In [1]:
import pandas as pd
#modelos
from sklearn.ensemble import AdaBoostClassifier, GradientBoostingClassifier
from xgboost import XGBClassifier      
from lightgbm import LGBMClassifier

#métricas
from sklearn.model_selection import RandomizedSearchCV
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score

import pickle
import warnings
warnings.filterwarnings('ignore')

##### Cargar datos

In [ ]:
train = pd.read_csv("../data/processed/04_diab_clean_train.csv")
test = pd.read_csv("../data/processed/04_diab_clean_test.csv")

##### Separar predictoras y objetivo

In [ ]:
X_train = train.drop("Outcome", axis=1)
y_train = train["Outcome"]

X_test = test.drop("Outcome", axis=1)
y_test = test["Outcome"]

#Comprobamos el balance y que siguen dividido el dataset convenientemente par el modelo
X_train.shape, X_test.shape, train['Outcome'].value_counts(normalize=True)

((614, 8),
 (154, 8),
 Outcome
 0    0.651466
 1    0.348534
 Name: proportion, dtype: float64)

##### Función para métricas de un modelo ya entrenado

Esta función recibe un modelo ya entrenado `model` y el nombre del modelo `name`, calcula sus predicciones sobre el conjunto de test y devolverá un Dataframe con accuracy, Precision, recall y F1. Esto nos permitirá comparar fácilmente distintos modelos en formato tabular 

In [ ]:
def calc_metrics_model(model, name, X_test, y_test):
    #prediccion del test
    y_pred = model.predict(X_test)
    #resultado métricas
    metric_df = pd.DataFrame({"Accuracy":[accuracy_score(y_test, y_pred)],
                              "Precision":[precision_score(y_test, y_pred)],
                              "Recall":[recall_score(y_test, y_pred)],
                              "F1-score":[f1_score(y_test, y_pred)]}, index=[name])
    return metric_df

#### Entreanmiento e hiperparametrización para todos los modelos boosting


In [ ]:
'''X_train, y_train --> datos de entrenamiento
   X_test, y_test --> datos de test
   n_iter --> número de combinaciones aleatorias de hiperparametros que probará cada moedlo
   cv --> número de folds/particiones que probará cada modelo para validación cruzada'''

def boosting_models(X_train, y_train, X_test, y_test, n_iter=50, cv=5):
    
    # nombre modelo : instancia del modelo
    models = {"AdaBoost":AdaBoostClassifier(random_state=42),
              "GradientBoosting":GradientBoostingClassifier(random_state=42),
              "XGBoost":XGBClassifier(eval_metric="logloss", random_state=42),#métrica que evalúa la calidad de las probabilidades predichas binarias
              "LightGBM":LGBMClassifier(random_state=42)}
    
    # definicion de hiperparametros para cada modelo
    params_grid = {"AdaBoost":{"n_estimators":[50, 100, 150, 200, 300, 500],
                               "learning_rate":[0.01, 0.05, 0.1, 0.2, 0.3]},                          
                   "GradientBoosting":{"n_estimators":[100, 200, 300, 400],
                                       "learning_rate":[0.01, 0.05, 0.1],
                                       "max_depth":[2, 3, 4],
                                       "subsample":[0.6, 0.8, 1.0]},
                   "XGBoost":{"n_estimators":[200, 300, 400, 500],
                              "learning_rate":[0.01, 0.03, 0.05, 0.1],
                              "max_depth":[2, 3, 4, 5],
                              "subsample":[0.6, 0.8, 1.0],
                              "colsample_bytree": [0.6, 0.8, 1.0]},
                   "LightGBM":{"n_estimators":[200, 400, 600, 800],
                               "learning_rate":[0.01, 0.03, 0.05, 0.1],
                               "max_depth":[-1, 3, 5, 7],
                               "num_leaves":[15, 31, 63, 127],
                               "subsample":[0.6, 0.8, 1.0],
                               "colsample_bytree": [0.6, 0.8, 1.0]}}
    # lista para guardar los df 
    results = []
    # itera sobre nombre e instancia en claves valor de models
    for name, base_model in models.items():
        search =RandomizedSearchCV(estimator=base_model,                 # instancia del modelo
                                   param_distributions=params_grid[name],# hiperparametros de la lista params_grid
                                   n_iter=n_iter,                        # iterciones param func   
                                   cv=cv,                                #cross validation param func
                                   scoring="recall",                     # criterio para elegir mejor modelo
                                   n_jobs=-1,                            # usa todos los cores posibles de la máquina   
                                   random_state=42)                      # semilla misma reproducción                   
        #entreno
        search.fit(X_train, y_train)
        
        # Mejor combinación de hiperparámetros segun scoring="recall"
        best_model = search.best_estimator_
        
        # llama a calc_metrics_model que calcula el entrenamiento de los modelos y devuelve un df 
        # que metemos en la lista results
        df_metrics = calc_metrics_model(best_model, name, X_test, y_test)
        results.append(df_metrics)
        
    # concatenamos todos los df obtenisdos         
    final_df = pd.concat(results)
    
    return final_df



In [ ]:
res_metrics_boosting = boosting_models(X_train, y_train, X_test, y_test)
res_metrics_boosting

[LightGBM] [Info] Number of positive: 171, number of negative: 320
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000064 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 574
[LightGBM] [Info] Number of data points in the train set: 491, number of used features: 8
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.348269 -> initscore=-0.626657
[LightGBM] [Info] Start training from score -0.626657
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Info] Number of positive: 171, number of negative: 320
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000081 seconds.
You can set `force_col_wise=true` to remove the overhe

Accuracy  Precision    Recall  F1-score
AdaBoost          0.772727   0.743590  0.537037  0.623656
GradientBoosting  0.746753   0.653061  0.592593  0.621359
XGBoost           0.733766   0.627451  0.592593  0.609524
LightGBM          0.759740   0.666667  0.629630  0.647619

#### Guardar en archivo metrics_diab.csv y guardado de objetos

In [ ]:
#cargar el archivo
diab_file = pd.read_csv("../models/metrics_diab.csv", index_col=0)

#añadir las métricas boostin
add_metrics = pd.concat([diab_file, res_metrics_boosting])

#Evitar duplicados al ejecutar el código
add_metrics = add_metrics[~add_metrics.index.duplicated(keep='last')]

#guardar
add_metrics.to_csv("../models/metrics_diab.csv", index=True)

add_metrics


Accuracy  Precision    Recall  F1-score
Decision Tree     0.766234   0.650000  0.722222  0.684211
Random Forest     0.759740   0.681818  0.555556  0.612245
AdaBoost          0.772727   0.743590  0.537037  0.623656
GradientBoosting  0.746753   0.653061  0.592593  0.621359
XGBoost           0.733766   0.627451  0.592593  0.609524
LightGBM          0.759740   0.666667  0.629630  0.647619

#### Conclusión

En este proyecto hemos entrenado y optimizado  varios modelos de boosting con el objetivo de compararlos con los modelos de arbol de decisión y bosque aleatorio para comprobar si alguno de ellos mejoraba las métricas obtenidas. 
Tras el anaálisis (accuracy, precision, recall y F1-score), el modelo que sigue ofreciendo mejor rendimiento global es el árbol de decision optimizado con GridSearchCV. Este modelo ya fue entrenado en el notebook `04_decision_tree_diabetes.ipynby` guardado con el nombre `diab_tree_classifier_crit-entro_maxdepth-5_minleaf-2_minsplit10_42`, dado que este modelo ya fue guardado, no tiene sentido hacerlo de nuevo. Los modelos de boosting que se han realizado han sido con fines comparativos, si en el futuro se actualizara el dataset y algún modelo de boosting superara al árbol de decisión, si se guardaría el modelo correspondiente.
 Viendo los resultados obtenidos nos podemos preguntar porque el modelo más simple es el que obtiene mejores resultados, esto tiene varias razones:
 * El dataset es pequeño, por lo que los modelos boosting no tienen suficiente información para construir patrones sin sobreajustar.
 * Las realciones entre predictoras y objetivo son directas, especialmente Glucosa, IMC y edad, por lo que el árbol de decisión las captura con facilidad
 * El árbol de decisón se a adptado mejor a *recall* (¿Cuantas personas que ***sí*** tienen  diabetes las detectó correctamente) que los modelos boosting que tienden a centrarse más en *accuracy*

 Dentro de los modelos boosting, tras la optimización, los resultados muestran que *LightGBM* es el más equilibrado, alcanzando un **recall** de 62% y un **F1_score** de 64%, lo que lo convierte el el mejor dentro del congunto boosting. *Adaboost* tiene la mejor **precison** 74% pero el **recall** más bajo 53%. En conjunto, aunque los modelos boosting nos aportan mejoras parciales, ninguno supera al árbol de decisión que es el modelo más fiable con un **F1_score** 68% y un **recall** de 72%